In [1]:
import torch
import torch.nn as nn
import plotly.express as ex
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import numpy as np
import json as js
import Extract
import scipy.signal as signal
from cytoolz import sliding_window
import scipy.optimize as optimize
import func
import GlobalSettings as Global
import _pickle as pickle
import rig_agnostic_encoding.functions.DataProcessingFunctions as Data

In [2]:
data = js.load(open("/home/nuoc/.config/unity3d/DefaultCompany/Procedural Animation/Test/multi_2_randRot.json", "r"))

In [3]:
df = Extract.ParseRawSequence(data)


In [4]:
def load_features_local(data, feature_list, sampling_step=5, frame_window=15, use_window=False):
    frames = data["frames"]
    clip = []
    keyJ = [i for i in range(len(frames[0])) if frames[0][i]["key"]]
    feature_dims = {}

    for f_id, f in enumerate(frames):
        if use_window:
            f_idx = np.arange(f-frame_window, f+frame_window, sampling_step, dtype=int)
        else:
            f_idx = [f_id]

        row = []
        for feature in feature_list:
            # KEY JOINTS ONLY FEATURES
            if feature == "phase_vec":
                row.append(np.concatenate([frames[idx][jj]["phase"].ravel() for jj in keyJ for idx in f_idx]))
            elif feature == "contact":
                row.append(np.concatenate([frames[idx][jj]["contact"].ravel() for jj in keyJ for idx in f_idx]))
            elif feature == "targetRotation" or feature == "targetPosition":
                row.append(np.concatenate(
                    [frames[idx][jj][feature].ravel() for jj in keyJ for idx in f_idx]))
            elif feature == "tPos" :
                row.append(np.concatenate(
                    [frames[idx][jj]["pos"] for jj in keyJ for idx in f_idx]))
            elif feature == "tRot":
                row.append(np.concatenate(
                    [frames[idx][jj]["rotMat"].ravel() for jj in keyJ for idx in f_idx]))
            # ALL JOINTS FEATURES
            elif feature == "rotMat":
                row.append(np.concatenate([jo["rotMat"].ravel() for jo in f]))
            elif feature == "isLeft" or feature == "chainPos" or feature == "geoDistanceNormalised":
                row.append(np.concatenate([[jo[feature]] for jo in f]))
            else:
                row.append(np.concatenate([jo[feature] for jo in f]))

            if feature not in feature_dims:
                feature_dims[feature] = row[-1].shape[0]

            assert(np.isnan(row[-1]).sum() == 0, "{} contains NaN".format(feature))

        row = np.concatenate(row)
        clip.append(row)
    return np.vstack(clip), feature_dims

<>:40: SyntaxWarning: assertion is always true, perhaps remove parentheses?
<>:40: SyntaxWarning: assertion is always true, perhaps remove parentheses?
<ipython-input-4-e258358db6b2>:40: SyntaxWarning: assertion is always true, perhaps remove parentheses?
  assert(np.isnan(row[-1]).sum() == 0, "{} contains NaN".format(feature))


# Positions

In [ ]:
features = ["pos"]
clip, dims = load_features_local(df, features)

In [17]:
pos = clip.reshape((-1, 31, 3))
x = np.arange(pos.shape[0])
fig = make_subplots(rows=3, cols=1, subplot_titles=["X", "Y", "Z"])
for i in range(3):
    for j in range(31):
        fig.add_trace(go.Scatter(x=x, y=pos[:, j, i], name="J"+str(j)), row=i+1, col=1)
fig.show()

# Position cost

In [19]:
features = ["posCost"]
clip, dims = load_features_local(df, features)

In [20]:
pos = clip.reshape((-1, 31, 3))
x = np.arange(pos.shape[0])
fig = make_subplots(rows=3, cols=1, subplot_titles=["X", "Y", "Z"])
for i in range(3):
    for j in range(31):
        fig.add_trace(go.Scatter(x=x, y=pos[:, j, i], name="J"+str(j)), row=i+1, col=1)
fig.show()


# Position cost value

In [21]:
features = ["posCostDistance"]
clip, dims = load_features_local(df, features)

In [22]:
pos = clip.reshape((-1, 31, 1))
x = np.arange(pos.shape[0])
fig = make_subplots(rows=1, cols=1, subplot_titles=["Distance"])
for j in range(31):
    fig.add_trace(go.Scatter(x=x, y=pos[:, j, 0], name="J"+str(j)), row=1, col=1)
fig.show()
# Position cost value

# Rotation cost angle

In [23]:
features = ["rotCostAngle"]
clip, dims = load_features_local(df, features)

In [24]:
pos = clip.reshape((-1, 31, 1))
x = np.arange(pos.shape[0])
fig = make_subplots(rows=1, cols=1, subplot_titles=["Rotation Angle"])
for j in range(31):
    fig.add_trace(go.Scatter(x=x, y=pos[:, j, 0], name="J"+str(j)), row=1, col=1)
fig.show()

# Velocity

In [5]:
features = ["velocity"]
velocity, dims = load_features_local(df, features)

In [41]:
velocity = velocity.reshape((-1, 31, 3))
x = np.arange(pos.shape[0])
fig = make_subplots(rows=3, cols=1, subplot_titles=["X", "Y", "Z"])
for i in range(3):
    for j in range(31):
        fig.add_trace(go.Scatter(x=x, y=velocity[:, j, i], name="J"+str(j)), row=i+1, col=1)
fig.show()

# Contact and phase

In [6]:
features = ["contact"]
block_fn, dims = load_features_local(df, features)



In [7]:
pos = block_fn.reshape((-1, 4))
x = np.arange(pos.shape[0])
fig = make_subplots(rows=1, cols=1, subplot_titles=["Contact"])
for j in range(4):
    fig.add_trace(go.Scatter(x=x, y=pos[:, j], name="J"+str(j)), row=1, col=1)
fig.show()

In [8]:
window_size_half = 15

block_fn2 = block_fn.T
velocity2 = velocity.T

Frames = block_fn2.shape[1]
t = np.arange(Frames)
normalised_block_fn = np.zeros_like(block_fn2, dtype=np.float32)

for ts in t:
    low = max(ts-window_size_half, 0)
    high = min(ts+window_size_half, Frames)
    window = np.arange(low, high)
    if len(window) < window_size_half*2:
        window = np.pad(window, (window_size_half*2-len(window),), mode='edge')
    slice = block_fn2[:, window]
    mean = np.mean(slice, axis=1)
    std = np.std(slice, axis=1)
    std[std == 0] = 1
    normalised_block_fn[:, ts] = (block_fn2[:, ts]-mean) / std

# normalised_block_fn = (block_fn2 - np.mean(block_fn2, axis=1, keepdims=True)) / np.std(block_fn2, axis=1, keepdims=True)
filter = signal.butter(3, .1, "low", analog=False, output="sos")
filtered = signal.sosfilt(filter, normalised_block_fn)

In [65]:
y = normalised_block_fn.T
x = np.arange(y.shape[0])
fig = make_subplots(rows=1, cols=1, subplot_titles=["Contact"])
for j in range(4):
    fig.add_trace(go.Scatter(x=x, y=y[:, j], name="J"+str(j)), row=1, col=1)
fig.show()



In [66]:
y = filtered.T
x = np.arange(y.shape[0])
fig = make_subplots(rows=1, cols=1, subplot_titles=["Contact"])
for j in range(4):
    fig.add_trace(go.Scatter(x=x, y=y[:, j], name="J"+str(j)), row=1, col=1)
fig.show()


In [58]:
def infer(a, f, t, s, b):
    return a * np.sin(f * t - s) + b
def func(x, *args):
    a = x[0]
    f = x[1]
    s = x[2]
    b = x[3]

    t = args[0]
    y = args[1]
    return np.sqrt(np.sum(
        (infer(a,f,t,s,b)-y[t])**2) / float(len(t)))


In [59]:
y = np.copy(filtered[2,:])
Frames = len(y)
pi = 2 * np.pi
a = np.random.normal(0,1,Frames)
f = np.random.normal(0, pi, Frames)
s = np.random.normal(0,1e-3, Frames)
b = np.random.normal(0,1e-3, Frames)
t = np.arange(Frames)

results = []
for ts in t:
    low = max(ts-12, 0)
    high = min(ts+12, Frames)
    window = np.arange(low, high)
    if len(window) < window_size_half*2:
        window = np.pad(window, (window_size_half*2-len(window),), mode='edge')
    slice = t[window]

    param = [a[ts], f[ts], s[ts], b[ts]]
    r = optimize.minimize(func, param, args=(slice, y), method="BFGS")
    results.append(r)

In [65]:
amp = np.asarray([res.x[0] for res in results], dtype=np.float32)
freq = np.asarray([res.x[1] for res in results], dtype=np.float32)
phase = np.asarray([res.x[2] for res in results], dtype=np.float32)
bias = np.asarray([res.x[3] for res in results], dtype=np.float32)


In [66]:
fig = go.Figure()
y2 = [infer(amp[ts], freq[ts], ts, phase[ts], bias[ts]) for ts in t]
fig.add_trace(go.Scatter(x=t, y=y2, name="optimised"))
fig.add_trace(go.Scatter(x=t, y=y, name="original"))
fig.show()

In [68]:
phase_vec = [(freq[ts]*ts - phase[ts])%pi for ts in t]
amp2 = (amp - np.mean(amp)) / np.std(amp)
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=phase_vec, name="phase"))
fig.add_trace(go.Bar(x=t, y=np.abs(amp2), name="amplitude"))
fig.show()

In [70]:
velocity = velocity.reshape((-1, 31, 3))
velo_mag = velocity[:, 14]
velo_mag = np.sqrt(np.sum(velo_mag**2, axis=1))
velo_mag *= np.diff(np.asarray(phase_vec), prepend=0)
phase_vec_sin = velo_mag * amp2 * np.sin(phase_vec)
phase_vec_cos = velo_mag * amp2 * np.cos(phase_vec)

In [93]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=phase_vec_sin, name="sin"))
fig.add_trace(go.Scatter(x=t, y=phase_vec_cos, name="cos"))
fig.show()


In [101]:
# ugly solution

y = np.copy(filtered[2,:])
sin_y = np.sin(y)
cos_y = np.cos(y)
amp_sin = np.diff(sin_y, prepend=0)
amp_cos = np.diff(cos_y, prepend=0)
amp_diff = np.diff(amp, prepend=0)
amp_cos[0]=0
# velocity = velocity.reshape((-1, 31, 3))
# velo_mag = velocity[:, 14]
# velo_mag = np.sqrt(np.sum(velo_mag**2, axis=1))

fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=y, name="y "))
fig.add_trace(go.Scatter(x=t, y=sin_y, name="sin y "))
fig.add_trace(go.Scatter(x=t, y=sin_y*(amp+1)*5, name="sin y * amp "))
fig.add_trace(go.Bar(x=t, y=amp, name="amp"))
fig.show()

In [106]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=y, name="y"))
fig.add_trace(go.Scatter(x=t, y=sin_y*amp_sin, name="sin phase"))
fig.add_trace(go.Scatter(x=t, y=cos_y*amp_cos, name="cos phase"))
fig.add_trace(go.Bar(x=t, y=amp_sin, name="amp sin"))
fig.add_trace(go.Bar(x=t, y=amp_cos, name="amp cos"))
fig.show()




In [104]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=t, y=np.sin(y)*velo_mag, name="sin phase"))
fig.add_trace(go.Scatter(x=t, y=np.cos(y)*velo_mag, name="cos phase"))
fig.show()
